In [1]:
import requests
from bs4 import BeautifulSoup
from selenium import webdriver
import pandas as pd
import itertools
import re

## Preparation for Web Scarpping

In [2]:
#Define header
header = {"user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/106.0.0.0 Safari/537.36"}

In [3]:
#Preparing list of files
page_list = [*range(1,101)]
city_list = ['dki-jakarta','bekasi','tangerang','bogor','depok']
place_category = ['apartemen', 'rumah']
place_ownership = ['jual', 'sewa']

In [5]:
df.head()

place_name  \
0  Andre Tjhia Meruya Scandinavian House Uk 5x24 ...   
1  Andre Tjhia Tanjung Duren Rumah Baru 3 Lantai ...   
2  Rumah murah minimalis 2 lantai deket transmart...   
3          Rumah Taman Surya 3 Luas 200m2 Harga Nego   
4  Rumah Murah di Jagakarsa Jakarta Selatan Siap ...   

                         address bedroom    area           price  \
0          Meruya, Jakarta Barat       3  120 m²   Rp 2,4 Miliar   
1   Tanjung Duren, Jakarta Barat       3   33 m²  Rp 1,35 Miliar   
2  Pondok Ranggon, Jakarta Timur       3   45 m²     Rp 595 Juta   
3     Taman Surya, Jakarta Barat       4  200 m²     Rp 4 Miliar   
4     Jagakarsa, Jakarta Selatan       3   61 m²   Rp 1,2 Miliar   

                         mortage  category  \
0  Cicilan : 17 Jutaan per bulan  category   
1   Cicilan : 9 Jutaan per bulan  category   
2   Cicilan : 4 Jutaan per bulan  category   
3  Cicilan : 28 Jutaan per bulan  category   
4   Cicilan : 8 Jutaan per bulan  category   

                                         date_posted  
0  Andre Tjhia ParaLand PropertyDiperbarui sejak ...  
1  Andre Tjhia ParaLand PropertyDiperbarui sejak ...  
2          Abu Tsaqif Diperbarui sejak 05 Juni, 2023  
3            Willy KOKDiperbarui sejak 05 Juni, 2023  
4          Abdul GofarDiperbarui sejak 05 Juni, 2023

In [4]:
merged_df = pd.DataFrame()
for ownership, city, category, page in itertools.product(place_ownership,city_list, place_category, page_list):
    url = f'https://www.rumah123.com/{ownership}/{str(city)}/{category}/?page={str(page)}#qid~42eeef39-13df-4144-afa7-f1229e9827be'
    r = requests.get(url,headers=header)
    c = r.content
    page = BeautifulSoup(c, 'html.parser')
    all_city = page.find_all('div',class_='ui-organism-intersection__element intersection-card-container')
    place_name = []
    place_address = []
    building_area = []
    num_bedroom = []
    place_price = []
    place_mortage = []
    date_posted = []
    for i in all_city:
        try:
            name = i.find('a').find('h2').text
        except:
            name = None
        try:
            address = i.find('div', class_='card-featured__middle-section').find('span',text = re.compile(",")).text
        except:
            address = None
        try:
            bedroom = i.find('span', class_='attribute-text').text
        except:
            bedroom = None
        try:
            area = i.find('div', class_='attribute-info').find('span').text
        except:
            area = None
        try:
            price = i.find('div', class_='card-featured__middle-section__price').find('strong').text
        except:
            price = None
        try:
            mortage = i.find('div', class_='card-featured__middle-section__price').find('em').text.replace("Cicilan:", "").strip()
        except:
            mortage = None
        try:
            jadwal = i.find('div', class_='ui-organisms-card-r123-basic__bottom-section__agent').text
        except:
            jadwal = None
        place_name.append(name)
        place_address.append(address)
        num_bedroom.append(bedroom)
        building_area.append(area)
        place_price.append(price)
        place_mortage.append(mortage)
        date_posted.append(jadwal)
        df = pd.DataFrame({'place_name':place_name, 'address':place_address, 'bedroom':num_bedroom, 'area':building_area,
                                'price':place_price, 'mortage':place_mortage, 'category': category, 'date_posted':date_posted})
        # df.to_csv(os.path.join(path_output, f'{page}_{ownership}_{city}.csv'), index=False, sep = ';')
        merged_df = merged_df.append(df)

C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_9968\2481765341.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  merged_df = merged_df.append(df)
C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_9968\2481765341.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  merged_df = merged_df.append(df)
C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_9968\2481765341.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  merged_df = merged_df.append(df)
C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_9968\2481765341.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  merged_df = merged_df.append(df)
C:\Users\PutuAndika\AppData\Local\Temp\i

In [9]:
merged_df.to_csv('Scrap Output.csv')

In [2]:
merged_df = pd.read_csv("Scrap Output.csv")

C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_12856\4055348458.py:1: DtypeWarning: Columns (6) have mixed types. Specify dtype option on import or set low_memory=False.
  merged_df = pd.read_csv("Scrap Output.csv")


## Data Cleaning

In [3]:
#Drop null values
merged_df = merged_df.dropna()

#Drop duplicated values
merged_df = merged_df.drop_duplicates(subset='place_name')

In [4]:
#Assigning kecamatan and city
merged_df[['kecamatan','city']] = merged_df.address.str.split("," ,expand = True)
merged_df = merged_df.drop(columns=['address'])
merged_df.head()

Unnamed: 0                                         place_name  bedroom  \
0            0              termurah Ci Ditiro residence low zone      3.0   
2            1  Dijual murah dan cepat 2 bedroom kosong taman ...      2.0   
5            2  Dharmawangsa Residence, Tower 1, 4 Bedroom 350...      4.0   
9            3  Apartemen Taman Anggrek Residences Studio Furn...      1.0   
14           4    Apartement The Mansion Jasmine Tower Bellavista      3.0   

      area           price                         mortage   category  \
0   132 m²  Rp 5,25 Miliar   Cicilan : 37 Jutaan per bulan  apartemen   
2    50 m²   Rp 1,5 Miliar   Cicilan : 10 Jutaan per bulan  apartemen   
5   350 m²    Rp 17 Miliar  Cicilan : 121 Jutaan per bulan  apartemen   
9    26 m²     Rp 750 Juta    Cicilan : 5 Jutaan per bulan  apartemen   
14  119 m²   Rp 3,2 Miliar   Cicilan : 22 Jutaan per bulan  apartemen   

                                      date_posted       kecamatan  \
0            Mimie Diperbarui sejak 06 Juni, 2023         Menteng   
2            Alung Diperbarui sejak 05 Juni, 2023   Taman Anggrek   
5   Margie SahuburuaDiperbarui sejak 30 Mei, 2023  Kebayoran Baru   
9        Marina ZhoDiperbarui sejak 05 Juni, 2023   Taman Anggrek   
14          Sumitro Diperbarui sejak 30 Mei, 2023      Pademangan   

                city  
0      Jakarta Pusat  
2      Jakarta Barat  
5    Jakarta Selatan  
9      Jakarta Barat  
14     Jakarta Utara

In [5]:
#Cleaning price column
merged_df[['rp','new_price','number']] = merged_df['price'].str.split(" ", expand = True)
#Function to determine new price
def new_price(a):
    if 'Miliar' in a:
        return 1000000000
    else:
        return 1000000
merged_df['amount'] = merged_df.price.apply(lambda x: new_price(x))
merged_df['price'] = merged_df.price.str.replace("Rp","").str.replace("Miliar", "").str.replace("Juta","").str.replace(",",".").str.strip().astype('float')
merged_df['final_price'] = merged_df['price'] * merged_df['amount']
merged_df = merged_df.drop(columns = ['price', 'new_price', 'rp', 'amount'])

In [6]:
#Cleaning Area
merged_df['area'] = merged_df.area.str.replace("m²","").str.strip().astype('float')

In [10]:
merged_df.head()

Unnamed: 0                                         place_name  bedroom  \
0            0              termurah Ci Ditiro residence low zone      3.0   
2            1  Dijual murah dan cepat 2 bedroom kosong taman ...      2.0   
5            2  Dharmawangsa Residence, Tower 1, 4 Bedroom 350...      4.0   
9            3  Apartemen Taman Anggrek Residences Studio Furn...      1.0   
14           4    Apartement The Mansion Jasmine Tower Bellavista      3.0   

     area                         mortage   category  \
0   132.0   Cicilan : 37 Jutaan per bulan  apartemen   
2    50.0   Cicilan : 10 Jutaan per bulan  apartemen   
5   350.0  Cicilan : 121 Jutaan per bulan  apartemen   
9    26.0    Cicilan : 5 Jutaan per bulan  apartemen   
14  119.0   Cicilan : 22 Jutaan per bulan  apartemen   

                                      date_posted       kecamatan  \
0            Mimie Diperbarui sejak 06 Juni, 2023         Menteng   
2            Alung Diperbarui sejak 05 Juni, 2023   Taman Anggrek   
5   Margie SahuburuaDiperbarui sejak 30 Mei, 2023  Kebayoran Baru   
9        Marina ZhoDiperbarui sejak 05 Juni, 2023   Taman Anggrek   
14          Sumitro Diperbarui sejak 30 Mei, 2023      Pademangan   

                city  number   final_price  
0      Jakarta Pusat  Miliar  5.250000e+09  
2      Jakarta Barat  Miliar  1.500000e+09  
5    Jakarta Selatan  Miliar  1.700000e+10  
9      Jakarta Barat    Juta  7.500000e+08  
14     Jakarta Utara  Miliar  3.200000e+09

## Cleaning date posted

In [7]:
merged_df[['Nama','Date Posted']] = merged_df['date_posted'].str.split("sejak", expand=True)

In [8]:
merged_df['Date Posted'] = merged_df['Date Posted'].str.strip().str.replace(",","").str.strip()

In [9]:
merged_df[['day','month','year']] = merged_df['Date Posted'].str.split(" ", expand=True)

In [17]:
merged_df.head()

Unnamed: 0                                         place_name  bedroom  \
0            0              termurah Ci Ditiro residence low zone      3.0   
2            1  Dijual murah dan cepat 2 bedroom kosong taman ...      2.0   
5            2  Dharmawangsa Residence, Tower 1, 4 Bedroom 350...      4.0   
9            3  Apartemen Taman Anggrek Residences Studio Furn...      1.0   
14           4    Apartement The Mansion Jasmine Tower Bellavista      3.0   

     area                         mortage   category  \
0   132.0   Cicilan : 37 Jutaan per bulan  apartemen   
2    50.0   Cicilan : 10 Jutaan per bulan  apartemen   
5   350.0  Cicilan : 121 Jutaan per bulan  apartemen   
9    26.0    Cicilan : 5 Jutaan per bulan  apartemen   
14  119.0   Cicilan : 22 Jutaan per bulan  apartemen   

                                      date_posted       kecamatan  \
0            Mimie Diperbarui sejak 06 Juni, 2023         Menteng   
2            Alung Diperbarui sejak 05 Juni, 2023   Taman Anggrek   
5   Margie SahuburuaDiperbarui sejak 30 Mei, 2023  Kebayoran Baru   
9        Marina ZhoDiperbarui sejak 05 Juni, 2023   Taman Anggrek   
14          Sumitro Diperbarui sejak 30 Mei, 2023      Pademangan   

                city  number   final_price                         Nama  \
0      Jakarta Pusat  Miliar  5.250000e+09            Mimie Diperbarui    
2      Jakarta Barat  Miliar  1.500000e+09            Alung Diperbarui    
5    Jakarta Selatan  Miliar  1.700000e+10  Margie SahuburuaDiperbarui    
9      Jakarta Barat    Juta  7.500000e+08        Marina ZhoDiperbarui    
14     Jakarta Utara  Miliar  3.200000e+09          Sumitro Diperbarui    

     Date Posted day month  year  
0   06 Juni 2023  06  Juni  2023  
2   05 Juni 2023  05  Juni  2023  
5    30 Mei 2023  30   Mei  2023  
9   05 Juni 2023  05  Juni  2023  
14   30 Mei 2023  30   Mei  2023

In [19]:
merged_df.month.unique()

array(['Juni', 'Mei', 'Desember', 'Februari', 'April', 'Maret', 'Januari'],
      dtype=object)

In [10]:
list_month = ['06', '05', '12', '02', '04', '03',
       '01']
merged_df['month'] = merged_df['month'].replace(merged_df['month'].unique(), list_month)
merged_df['date'] = merged_df['day'] + '/' +merged_df['month']+'/'+merged_df['year']

In [22]:
merged_df.columns

Index(['Unnamed: 0', 'place_name', 'bedroom', 'area', 'mortage', 'category',
       'date_posted', 'kecamatan', 'city', 'number', 'final_price', 'Nama',
       'Date Posted', 'day', 'month', 'year', 'date'],
      dtype='object')

In [13]:
merged_df = merged_df.drop(columns=['Unnamed: 0','Date Posted', 'day', 'month', 'year','date_posted','Nama'])
merged_df.head()

KeyError: "['Unnamed: 0', 'Date Posted', 'day', 'month', 'year', 'date_posted', 'Nama'] not found in axis"

In [14]:
merged_df.head()

place_name  bedroom   area  \
0               termurah Ci Ditiro residence low zone      3.0  132.0   
2   Dijual murah dan cepat 2 bedroom kosong taman ...      2.0   50.0   
5   Dharmawangsa Residence, Tower 1, 4 Bedroom 350...      4.0  350.0   
9   Apartemen Taman Anggrek Residences Studio Furn...      1.0   26.0   
14    Apartement The Mansion Jasmine Tower Bellavista      3.0  119.0   

              mortage   category       kecamatan              city  number  \
0    37 Jutaan  bulan  apartemen         Menteng     Jakarta Pusat  Miliar   
2    10 Jutaan  bulan  apartemen   Taman Anggrek     Jakarta Barat  Miliar   
5   121 Jutaan  bulan  apartemen  Kebayoran Baru   Jakarta Selatan  Miliar   
9     5 Jutaan  bulan  apartemen   Taman Anggrek     Jakarta Barat    Juta   
14   22 Jutaan  bulan  apartemen      Pademangan     Jakarta Utara  Miliar   

     final_price        date  
0   5.250000e+09  06/06/2023  
2   1.500000e+09  05/06/2023  
5   1.700000e+10  30/05/2023  
9   7.500000e+08  05/06/2023  
14  3.200000e+09  30/05/2023

In [19]:
merged_df['mortage'] = merged_df.mortage.str.replace("Cicilan : ","").str.replace(" per ","").str.strip()


In [22]:
merged_df.mortage.unique()

array(['37 Jutaan  bulan', '10 Jutaan  bulan', '121 Jutaan  bulan',
       '5 Jutaan  bulan', '22 Jutaan  bulan', '26 Jutaan  bulan',
       '35 Jutaan  bulan', '6 Jutaan  bulan', '25 Jutaan  bulan',
       '3 Jutaan  bulan', '12 Jutaan  bulan', '28 Jutaan  bulan',
       '53 Jutaan  bulan', '11 Jutaan  bulan', '42 Jutaan  bulan',
       '21 Jutaan  bulan', '1 Jutaan  bulan', '100 Jutaan  bulan',
       '15 Jutaan  bulan', '4 Jutaan  bulan', '9 Jutaan  bulan',
       '45 Jutaan  bulan', '16 Jutaan  bulan', '20 Jutaan  bulan',
       '30 Jutaan  bulan', '71 Jutaan  bulan', '23 Jutaan  bulan',
       '2 Jutaan  bulan', '14 Jutaan  bulan', '50 Jutaan  bulan',
       '164 Jutaan  bulan', '62 Jutaan  bulan', '17 Jutaan  bulan',
       '24 Jutaan  bulan', '18 Jutaan  bulan', '8 Jutaan  bulan',
       '13 Jutaan  bulan', '39 Jutaan  bulan', '64 Jutaan  bulan',
       '34 Jutaan  bulan', '49 Jutaan  bulan', '7 Jutaan  bulan',
       '32 Jutaan  bulan', '118 Jutaan  bulan', '179 Jutaan  bulan',

In [23]:
merged_df[['number','category','excess_space','monthly']] = merged_df['mortage'].str.split(" ",expand=True)
merged_df.head()

place_name  bedroom   area  \
0               termurah Ci Ditiro residence low zone      3.0  132.0   
2   Dijual murah dan cepat 2 bedroom kosong taman ...      2.0   50.0   
5   Dharmawangsa Residence, Tower 1, 4 Bedroom 350...      4.0  350.0   
9   Apartemen Taman Anggrek Residences Studio Furn...      1.0   26.0   
14    Apartement The Mansion Jasmine Tower Bellavista      3.0  119.0   

              mortage category       kecamatan              city number  \
0    37 Jutaan  bulan   Jutaan         Menteng     Jakarta Pusat     37   
2    10 Jutaan  bulan   Jutaan   Taman Anggrek     Jakarta Barat     10   
5   121 Jutaan  bulan   Jutaan  Kebayoran Baru   Jakarta Selatan    121   
9     5 Jutaan  bulan   Jutaan   Taman Anggrek     Jakarta Barat      5   
14   22 Jutaan  bulan   Jutaan      Pademangan     Jakarta Utara     22   

     final_price        date excess_space monthly  
0   5.250000e+09  06/06/2023                bulan  
2   1.500000e+09  05/06/2023                bulan  
5   1.700000e+10  30/05/2023                bulan  
9   7.500000e+08  05/06/2023                bulan  
14  3.200000e+09  30/05/2023                bulan

In [24]:
merged_df.category.unique()

array(['Jutaan', 'Ribuan', 'Miliaran'], dtype=object)

In [25]:
merged_df.monthly.unique()

array(['bulan'], dtype=object)

In [26]:
def mortage_category(a):
    if a == 'Jutaan':
        return 1000000
    elif a == 'Ribuan':
        return 1000
    else:
        return 1000000000
merged_df['number_cat'] = merged_df.category.apply(lambda x: mortage_category(x))

In [27]:
merged_df.head()

place_name  bedroom   area  \
0               termurah Ci Ditiro residence low zone      3.0  132.0   
2   Dijual murah dan cepat 2 bedroom kosong taman ...      2.0   50.0   
5   Dharmawangsa Residence, Tower 1, 4 Bedroom 350...      4.0  350.0   
9   Apartemen Taman Anggrek Residences Studio Furn...      1.0   26.0   
14    Apartement The Mansion Jasmine Tower Bellavista      3.0  119.0   

              mortage category       kecamatan              city number  \
0    37 Jutaan  bulan   Jutaan         Menteng     Jakarta Pusat     37   
2    10 Jutaan  bulan   Jutaan   Taman Anggrek     Jakarta Barat     10   
5   121 Jutaan  bulan   Jutaan  Kebayoran Baru   Jakarta Selatan    121   
9     5 Jutaan  bulan   Jutaan   Taman Anggrek     Jakarta Barat      5   
14   22 Jutaan  bulan   Jutaan      Pademangan     Jakarta Utara     22   

     final_price        date excess_space monthly  number_cat  
0   5.250000e+09  06/06/2023                bulan     1000000  
2   1.500000e+09  05/06/2023                bulan     1000000  
5   1.700000e+10  30/05/2023                bulan     1000000  
9   7.500000e+08  05/06/2023                bulan     1000000  
14  3.200000e+09  30/05/2023                bulan     1000000

In [28]:
merged_df['number'] = merged_df.number.astype('float')
merged_df['final_mortage_monthly'] = merged_df['number'] * merged_df['number_cat']
merged_df = merged_df.drop(columns=['number_cat', 'excess_space', 'number', 'mortage', 'category'])
merged_df.head()

place_name  bedroom   area  \
0               termurah Ci Ditiro residence low zone      3.0  132.0   
2   Dijual murah dan cepat 2 bedroom kosong taman ...      2.0   50.0   
5   Dharmawangsa Residence, Tower 1, 4 Bedroom 350...      4.0  350.0   
9   Apartemen Taman Anggrek Residences Studio Furn...      1.0   26.0   
14    Apartement The Mansion Jasmine Tower Bellavista      3.0  119.0   

         kecamatan              city   final_price        date monthly  \
0          Menteng     Jakarta Pusat  5.250000e+09  06/06/2023   bulan   
2    Taman Anggrek     Jakarta Barat  1.500000e+09  05/06/2023   bulan   
5   Kebayoran Baru   Jakarta Selatan  1.700000e+10  30/05/2023   bulan   
9    Taman Anggrek     Jakarta Barat  7.500000e+08  05/06/2023   bulan   
14      Pademangan     Jakarta Utara  3.200000e+09  30/05/2023   bulan   

    final_mortage_monthly  
0              37000000.0  
2              10000000.0  
5             121000000.0  
9               5000000.0  
14             22000000.0